<a href="https://colab.research.google.com/github/ajustus-stack/AD688-GenAI/blob/main/A01_Gen_AI_Class_ajustus_SP26.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [3]:
import os

from google.colab import drive
drive.mount('/content/drive')

data_dir = '/content/drive/MyDrive/AD688GenAI/SEC-10K-2024'


print("drive mounted successfully. Data dricatory found")


Mounted at /content/drive
drive mounted successfully. Data dricatory found


In [4]:
import os
os.listdir("/content/drive/MyDrive")

['Colab Notebooks', 'CV_Aston Justus_2026.pdf', 'AD688 GenAI']

In [5]:
from pathlib import Path

# SEC_DIR = Path("../../data/SEC-10K-2024")
DATA_ROOT = Path("/content/drive/MyDrive/AD688 GenAI")
SEC_DIR = DATA_ROOT / "SEC-10K-2024"

assert SEC_DIR.exists(), "SEC data folder not found. Check Drive mount."

sec_files = list(SEC_DIR.glob("*.txt"))
print(f"Found {len(sec_files)} SEC filings")

Found 7754 SEC filings


In [6]:
sample_text=sec_files[0].read_text(encoding="utf-8")
print(sample_text[:1500])

<Header>
<FileStats>
    <FileName>20240927_10-K_edgar_data_1853044_0001829126-24-006527.txt</FileName>
    <GrossFileSize>12647701</GrossFileSize>
    <NetFileSize>724193</NetFileSize>
    <NonText_DocumentType_Chars>2010573</NonText_DocumentType_Chars>
    <HTML_Chars>4217690</HTML_Chars>
    <XBRL_Chars>2308433</XBRL_Chars>
    <XML_Chars>2974304</XML_Chars>
    <N_Exhibits>23</N_Exhibits>
</FileStats>
<SEC-Header>
0001829126-24-006527.hdr.sgml : 20240927
<ACCEPTANCE-DATETIME>20240927170051
ACCESSION NUMBER:		0001829126-24-006527
CONFORMED SUBMISSION TYPE:	10-K
PUBLIC DOCUMENT COUNT:		143
CONFORMED PERIOD OF REPORT:	20240331
FILED AS OF DATE:		20240927
DATE AS OF CHANGE:		20240927

FILER:

	COMPANY DATA:	
		COMPANY CONFORMED NAME:			Aeries Technology, Inc.
		CENTRAL INDEX KEY:			0001853044
		STANDARD INDUSTRIAL CLASSIFICATION:	SERVICES-MANAGEMENT CONSULTING SERVICES [8742]
		ORGANIZATION NAME:           	07 Trade & Services
		IRS NUMBER:				000000000
		FISCAL YEAR END:			0331

	FILI

In [7]:
import nltk
nltk.download ("punkt_tab")
from nltk.tokenize import sent_tokenize
sentences = sent_tokenize(sample_text)
print (f"Number of sentences: (len(sentences)) ")
sentences[:5]

[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt_tab.zip.


Number of sentences: (len(sentences)) 


['<Header>\n<FileStats>\n    <FileName>20240927_10-K_edgar_data_1853044_0001829126-24-006527.txt</FileName>\n    <GrossFileSize>12647701</GrossFileSize>\n    <NetFileSize>724193</NetFileSize>\n    <NonText_DocumentType_Chars>2010573</NonText_DocumentType_Chars>\n    <HTML_Chars>4217690</HTML_Chars>\n    <XBRL_Chars>2308433</XBRL_Chars>\n    <XML_Chars>2974304</XML_Chars>\n    <N_Exhibits>23</N_Exhibits>\n</FileStats>\n<SEC-Header>\n0001829126-24-006527.hdr.sgml : 20240927\n<ACCEPTANCE-DATETIME>20240927170051\nACCESSION NUMBER:\t\t0001829126-24-006527\nCONFORMED SUBMISSION TYPE:\t10-K\nPUBLIC DOCUMENT COUNT:\t\t143\nCONFORMED PERIOD OF REPORT:\t20240331\nFILED AS OF DATE:\t\t20240927\nDATE AS OF CHANGE:\t\t20240927\n\nFILER:\n\n\tCOMPANY DATA:\t\n\t\tCOMPANY CONFORMED NAME:\t\t\tAeries Technology, Inc.\n\t\tCENTRAL INDEX KEY:\t\t\t0001853044\n\t\tSTANDARD INDUSTRIAL CLASSIFICATION:\tSERVICES-MANAGEMENT CONSULTING SERVICES [8742]\n\t\tORGANIZATION NAME:           \t07 Trade & Services\n\

In [8]:
import re
def extract_sic(text):
  match = re.search(r"SIC\s: \s*(\d{4})", text)
  return match.group(1) if match else None

In [9]:
def extract_section(text, start_pattern, end_pattern):
  start = re.search(start_pattern, text, re.IGNORECASE)
  end = re.search(end_pattern, text, re.IGNORECASE)
  if start and end and start.start()<end.start():
    return text[start.end():end.start()].strip()
    return ""

In [10]:
selected_files = sec_files

In [11]:
import pandas as pd
records = []

for fname in selected_files:
  path = os.path.join(data_dir, fname)

  try:
    with open(path, "r", encoding="utf-8", errors="ignor") as f:
      text = f.read()

    records.append({
        "file": fname,
        "raw_text": text
    })

  except Exception as e:
    records.append({
        "file": fname,
        "raw_text": None,
        "ingest_error":str(e)
    })

df = pd.DataFrame(records)
print(f"files ingested: {len(df)}")

df.head(2).style.hide(axis='index')

files ingested: 7754


extract Item 1a - Risk Factors  and Item 7 - MD&A

In [12]:
import re

def remove_sec_preamble(text):
  #pattern = r"UNITED STATES\s + SECURITIES AND EXCHANGE COMMISSION" #we can decide which part to delete and which part to keep. It's up to us.
  pattern = r"DOCUMENTS INCORPORATED BY REFERENCE"
  match = re.search(pattern, text, flags=re.IGNORECASE)
  if match:
    return text[match.start():]
  else:
    return text #fallback: return to original if pahse not found
df["text_no_preamble"] = df["raw_text"].apply(remove_sec_preamble)

In [13]:
import re

# 1. Redefine extract_section to ensure it handles missing sections
def extract_section(text, start_pattern, end_pattern):
    if not isinstance(text, str): return ""

    # Search for start and end patterns
    start = re.search(start_pattern, text, re.IGNORECASE)
    end = re.search(end_pattern, text, re.IGNORECASE)

    # Valid extraction case
    if start and end and start.start() < end.start():
        return text[start.end():end.start()].strip()

    # Fallback if patterns not found or order is wrong
    return ""

# 2. Define Regex Patterns for Item 1A and Item 7
# Pattern for Item 1A (Risk Factors) -> Ends at Item 1B
risk_start = r"ITEM\s+1A\.?\s+RISK\s+FACTORS"
risk_end = r"ITEM\s+1B\.?\s+UNRESOLVED|ITEM\s+2\.?\s+Properties"

# Pattern for Item 7 (MD&A) -> Ends at Item 7A or Item 8
mda_start = r"ITEM\s+7\.?\s+MANAGEMENT"
mda_end = r"ITEM\s+(?:7A\.?\s+Quantitative|8\.?\s+Financial)"

# 3. Apply to the DataFrame
print("Extracting Risk Factors (Item 1A)...")
df['item_1a'] = df['text_no_preamble'].apply(lambda x: extract_section(x, risk_start, risk_end))

print("Extracting MD&A (Item 7)...")
df['item_7'] = df['text_no_preamble'].apply(lambda x: extract_section(x, mda_start, mda_end))

# 4. Filter and Verify
# Create a clean dataframe with only files that had valid extractions
df_clean = df[ (df['item_1a'].str.len() > 100) & (df['item_7'].str.len() > 100) ].copy()

print(f"Extraction complete.")
print(f"Original Row Count: {len(df)}")
print(f"Rows with valid 1A and 7 content: {len(df_clean)}")

# Preview the data
df_clean[['file', 'item_1a', 'item_7']].head(3)

Extracting Risk Factors (Item 1A)...
Extracting MD&A (Item 7)...
Extraction complete.
Original Row Count: 7754
Rows with valid 1A and 7 content: 340


file  \
4   /content/drive/MyDrive/AD688 GenAI/SEC-10K-202...   
36  /content/drive/MyDrive/AD688 GenAI/SEC-10K-202...   
77  /content/drive/MyDrive/AD688 GenAI/SEC-10K-202...   

                                              item_1a  \
4   5 Risks Related to the Financial Position and ...   
36  in this Annual Report. \n Forward-Looking Stat...   
77  of this report. \n We derive many of our forwa...   

                                               item_7  
4   'S DISCUSSION AND ANALYSIS OF FINANCIAL CONDIT...  
36  s Discussion and Analysis of Financial Conditi...  
77  s Discussion and Analysis of Financial Conditi...

In [14]:
def clean_text (text):
  text = re.sub(r"\s+"," ", text)
  text = re.sub(r"[^A-Za-z0-9\.,;:\-\(\)\s]", "", text)
  return text.strip()

df["item_1a_clean"]=df["item_1a"].apply(clean_text)
df["item_7_clean"]=df["item_7"].apply(clean_text)
df[['file', 'item_1a_clean', 'item_7_clean']].head(2).style.hide(axis='index')

Sentence Processing

In [15]:
def sentence_split (text):
  return re.split(r"(?<=[.!?])\s+", text)

df["item_1a_sentences"] = df["item_1a_clean"].apply(sentence_split)
df["item_7_sentences"] = df["item_7_clean"].apply(sentence_split)
df[['file', 'item_1a_sentences', 'item_7_sentences']].head(2)

file item_1a_sentences  \
0  /content/drive/MyDrive/AD688 GenAI/SEC-10K-202...              [14]   
1  /content/drive/MyDrive/AD688 GenAI/SEC-10K-202...                []   

                                    item_7_sentences  
0  [s Discussion and Analysis of Financial Condit...  
1                                                 []

In [16]:
df[["item_1a_sentences", "item_7_sentences"]].head(2)

item_1a_sentences                                   item_7_sentences
0              [14]  [s Discussion and Analysis of Financial Condit...
1                []                                                 []

# Feature Engineering

In [17]:
# Minimum length threshold (characters)
MIN_LEN = 300

df["item_1a_len"] = df["item_1a_clean"].str.len()
df["item_7_len"] = df["item_7_clean"].str.len()


mask = (df["item_1a_len"] >= MIN_LEN) | (df["item_7_len"] >= MIN_LEN)

# 3. Filtern
bad_docs = df[~mask]
good_docs = df[mask].copy()

print(f"Documents dropped (beide zu kurz): {len(bad_docs)}")
print(f"Documents kept (mindestens einer lang genug): {len(good_docs)}")


Documents dropped (beide zu kurz): 7095
Documents kept (mindestens einer lang genug): 659


In [18]:
import re

def extract_sic_code (text:str) -> str | None:
  """
  Extrahiert den 4-stelligen SIC-Code aus dem SEC 10-K Text.
  Berücksichtigt das Format: STANDARD INDUSTRIAL CLASSIFICATION : TEXT [3724]
  """
  patterns = [
      # Sucht nach SIC : gefolgt von 4 Ziffern
      r"SIC\s*:\s*(\d{4})",
      # Sucht nach dem langen Namen, ignoriert Text bis zu den Klammern [3724]
      r"STANDARD\s*INDUSTRIAL\s*CLASSIFICATION\s*[:\-]?.*?\[(\d{4})\]",
      # Fallback: Sucht einfach nach dem Muster SIC gefolgt von Text und [4 Ziffern]
      r"SIC.*?\[(\d{4})\]"
    ]

  for pat in patterns:
    match = re.search(pat, text, re.IGNORECASE)
    if match:
      return match.group(1)

  return(None)

# ectract SEC code from raw text and populate it in colum
good_docs["sic_code"] = good_docs["raw_text"].apply(extract_sic_code)
good_docs.head(2)

file  \
4   /content/drive/MyDrive/AD688 GenAI/SEC-10K-202...   
20  /content/drive/MyDrive/AD688 GenAI/SEC-10K-202...   

                                             raw_text  \
4   <Header>\n<FileStats>\n    <FileName>20240716_...   
20  <Header>\n<FileStats>\n    <FileName>20240701_...   

                                     text_no_preamble  \
4   <Header>\n<FileStats>\n    <FileName>20240716_...   
20  <Header>\n<FileStats>\n    <FileName>20240701_...   

                                              item_1a  \
4   5 Risks Related to the Financial Position and ...   
20  6 Item 2 Description of Property 6 Item 3. Leg...   

                                               item_7  \
4   'S DISCUSSION AND ANALYSIS OF FINANCIAL CONDIT...   
20  s Discussion and Analysis Of Financial Conditi...   

                                        item_1a_clean  \
4   5 Risks Related to the Financial Position and ...   
20  6 Item 2 Description of Property 6 Item 3. Leg...   

                                         item_7_clean  \
4   S DISCUSSION AND ANALYSIS OF FINANCIAL CONDITI...   
20  s Discussion and Analysis Of Financial Conditi...   

                                    item_1a_sentences  \
4   [5 Risks Related to the Financial Position and...   
20  [6 Item 2 Description of Property 6 Item 3., L...   

                                     item_7_sentences  item_1a_len  \
4   [S DISCUSSION AND ANALYSIS OF FINANCIAL CONDIT...          210   
20  [s Discussion and Analysis Of Financial Condit...        15096   

    item_7_len sic_code  
4        76817     1700  
20          76     5961

In [19]:
# Unique SIC codes from sic_code Column
good_docs["sic_code"].unique()

array(['1700', '5961', '6221', '2834', '3669', '3679', '3533', '2211',
       '1040', '3845', '3480', '7372', '3578', '7389', '6552', '3310',
       '6798', '6770', '0200', '2844', '3910', '2835', '2711', '3572',
       '5960', '3827', '3990', '2833', '6159', None, '2080', '3949',
       '5141', '5900', '1400', '3661', '3412', '3823', '3690', '4911',
       '3663', '3674', '5122', '5812', '2870', '3829', '2836', '1531',
       '3312', '5051', '5072', '2070', '4941', '3317', '3442', '8062',
       '3576', '3841', '3360', '1311', '7990', '6036', '5990', '3724',
       '7374', '5411', '7200', '6513', '2800', '6141', '1000', '7370',
       '6500', '3272', '4832', '4813', '8742', '5040', '7373', '3842',
       '5150', '6794', '4412', '3711', '3564', '3621', '2040', '5130',
       '6035', '2890', '5140', '6211', '8200', '2200', '4513', '6022',
       '3559', '2340', '6199', '2860', '3826', '7371', '5311', '6021',
       '3569', '6799', '5912', '7320', '7359', '5331', '6111', '2000',
       '